In [1]:
import pandas as pd
import os

from helpers import get_combined_df, save_final_df_as_jsonl

In [2]:
DATA_DIR = "../data/"
PROCESSED_DIR = "../processed/"
FACET_DIR = "home_values_forecasts/"
FULL_DATA_DIR_PATH = os.path.join(DATA_DIR, FACET_DIR)
FULL_PROCESSED_DIR_PATH = os.path.join(PROCESSED_DIR, FACET_DIR)

In [3]:
data_frames = []

for filename in os.listdir(FULL_DATA_DIR_PATH):
    if filename.endswith(".csv"):
        print("processing " + filename)
        cur_df = pd.read_csv(os.path.join(FULL_DATA_DIR_PATH, filename))

        cols = ["Month Over Month %", "Quarter Over Quarter %", "Year Over Year %"]
        if filename.endswith("sm_sa_month.csv"):
            # print('Smoothed')
            cur_df.columns = list(cur_df.columns[:-3]) + [
                x + " (Smoothed) (Seasonally Adjusted)" for x in cols
            ]
        else:
            # print('Raw')
            cur_df.columns = list(cur_df.columns[:-3]) + cols
        cur_df["RegionName"] = cur_df["RegionName"].astype(str)

        data_frames.append(cur_df)


combined_df = get_combined_df(
    data_frames,
    [
        "RegionID",
        "RegionType",
        "SizeRank",
        "StateName",
        "BaseDate",
    ],
)

combined_df

processing Zip_zhvf_growth_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing Metro_zhvf_growth_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing Zip_zhvf_growth_uc_sfrcondo_tier_0.33_0.67_month.csv
processing Metro_zhvf_growth_uc_sfrcondo_tier_0.33_0.67_month.csv


RegionID  SizeRank RegionName RegionType StateName State        City  \
0         58001     30490        501        zip        NY    NY  Holtsville   
1         58002     30490        544        zip        NY    NY  Holtsville   
2         58196      7440       1001        zip        MA    MA      Agawam   
3         58197      3911       1002        zip        MA    MA     Amherst   
4         58198      8838       1003        zip        MA    MA     Amherst   
...         ...       ...        ...        ...       ...   ...         ...   
31849    827279      7779      72405        zip        AR    AR   Jonesboro   
31850    834213     30490      11437        zip        NY    NY    New York   
31851    845914      6361      85288        zip        AZ    AZ       Tempe   
31852    847854     39992      20598        zip        VA    VA   Arlington   
31853    847855     30490      34249        zip        FL    FL    Sarasota   

                                              Metro        CountyName  \
0             New York-Newark-Jersey City, NY-NJ-PA    Suffolk County   
1             New York-Newark-Jersey City, NY-NJ-PA    Suffolk County   
2                                   Springfield, MA    Hampden County   
3                                   Springfield, MA  Hampshire County   
4                                   Springfield, MA  Hampshire County   
...                                             ...               ...   
31849                                 Jonesboro, AR  Craighead County   
31850         New York-Newark-Jersey City, NY-NJ-PA     Queens County   
31851                     Phoenix-Mesa-Chandler, AZ   Maricopa County   
31852  Washington-Arlington-Alexandria, DC-VA-MD-WV  Arlington County   
31853             North Port-Sarasota-Bradenton, FL   Sarasota County   

         BaseDate  Month Over Month % (Smoothed) (Seasonally Adjusted)  \
0      2023-12-31                                                NaN    
1      2023-12-31                                                NaN    
2      2023-12-31                                                0.4    
3      2023-12-31                                                0.2    
4      2023-12-31                                                NaN    
...           ...                                                ...    
31849  2023-12-31                                                NaN    
31850  2023-12-31                                                NaN    
31851  2023-12-31                                                NaN    
31852  2023-12-31                                                NaN    
31853  2023-12-31                                                NaN    

       Quarter Over Quarter % (Smoothed) (Seasonally Adjusted)  \
0                                                    NaN        
1                                                    NaN        
2                                                    0.9        
3                                                    0.7        
4                                                    NaN        
...                                                  ...        
31849                                                NaN        
31850                                                NaN        
31851                                                NaN        
31852                                                NaN        
31853                                                NaN        

       Year Over Year % (Smoothed) (Seasonally Adjusted)  Month Over Month %  \
0                                                   NaN                -0.7   
1                                                   NaN                -0.7   
2                                                   3.2                -0.6   
3                                                   2.7                -0.6   
4                                                   NaN                -0.7   
...                                           

In [4]:
# Adjust columns
final_df = combined_df
final_df = combined_df.drop("StateName", axis=1)
final_df = final_df.rename(
    columns={
        "CountyName": "County",
        "BaseDate": "Date",
        "RegionName": "Region",
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
    }
)

# iterate over rows of final_df and populate State and City columns if the regionType is msa
for index, row in final_df.iterrows():
    if row["RegionType"] == "msa":
        regionName = row["Region"]
        # final_df.at[index, 'Metro'] = regionName

        city = regionName.split(", ")[0]
        final_df.at[index, "City"] = city

        state = regionName.split(", ")[1]
        final_df.at[index, "State"] = state

final_df

Region ID  Size Rank Region RegionType State        City  \
0          58001      30490    501        zip    NY  Holtsville   
1          58002      30490    544        zip    NY  Holtsville   
2          58196       7440   1001        zip    MA      Agawam   
3          58197       3911   1002        zip    MA     Amherst   
4          58198       8838   1003        zip    MA     Amherst   
...          ...        ...    ...        ...   ...         ...   
31849     827279       7779  72405        zip    AR   Jonesboro   
31850     834213      30490  11437        zip    NY    New York   
31851     845914       6361  85288        zip    AZ       Tempe   
31852     847854      39992  20598        zip    VA   Arlington   
31853     847855      30490  34249        zip    FL    Sarasota   

                                              Metro            County  \
0             New York-Newark-Jersey City, NY-NJ-PA    Suffolk County   
1             New York-Newark-Jersey City, NY-NJ-PA    Suffolk County   
2                                   Springfield, MA    Hampden County   
3                                   Springfield, MA  Hampshire County   
4                                   Springfield, MA  Hampshire County   
...                                             ...               ...   
31849                                 Jonesboro, AR  Craighead County   
31850         New York-Newark-Jersey City, NY-NJ-PA     Queens County   
31851                     Phoenix-Mesa-Chandler, AZ   Maricopa County   
31852  Washington-Arlington-Alexandria, DC-VA-MD-WV  Arlington County   
31853             North Port-Sarasota-Bradenton, FL   Sarasota County   

             Date  Month Over Month % (Smoothed) (Seasonally Adjusted)  \
0      2023-12-31                                                NaN    
1      2023-12-31                                                NaN    
2      2023-12-31                                                0.4    
3      2023-12-31                                                0.2    
4      2023-12-31                                                NaN    
...           ...                                                ...    
31849  2023-12-31                                                NaN    
31850  2023-12-31                                                NaN    
31851  2023-12-31                                                NaN    
31852  2023-12-31                                                NaN    
31853  2023-12-31                                                NaN    

       Quarter Over Quarter % (Smoothed) (Seasonally Adjusted)  \
0                                                    NaN        
1                                                    NaN        
2                                                    0.9        
3                                                    0.7        
4                                                    NaN        
...                                                  ...        
31849                                                NaN        
31850                                                NaN        
31851                                                NaN        
31852                                                NaN        
31853                                                NaN        

       Year Over Year % (Smoothed) (Seasonally Adjusted)  Month Over Month %  \
0                                                   NaN                -0.7   
1                                                   NaN                -0.7   
2                                                   3.2                -0.6   
3                                                   2.7                -0.6   
4                                                   NaN                -0.7   
...                                                 ...                 ...   
31849                                               NaN                -0.7   
31850                           

In [9]:
save_final_df_as_jsonl(FULL_PROCESSED_DIR_PATH, final_df)